# Ch 1: Overview
Welcome fellow traders! 

This is a Notebook on the My_Trading_Buddy. The aim of this project is to provide a assistance to a technical approach to trading on the ASX. The goal is for you to be equipt with the necessary tools to analyse market trends and simulate your personalised model! I have broken this up into chapters like a notebook. 

Best of Luck, 

Your trading buddy :)

## Ch 1.1: Import Packages

In [1]:
#import yfinance as yf
import pandas as pd
from pandas_datareader import data as pdr
import matplotlib.pyplot as plt
import math
import numpy as np

import datetime as dt

import plotly.offline as pyo
import plotly

import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)
pd.options.plotting.backend = 'plotly'

## Ch 1.2: Scrapping Data and Stock Overview 

In [2]:
# Define Start and End dates

end = dt.datetime.now()
#end = dt.datetime(2019,7,7)
start  = dt.datetime(2020,12,12)

In [3]:
# Define Stocks of interest

stocklist = ['MQG','CBA', 'NAB', 'WBC','BOQ','QAN','VAS', 'A200','ANZ']
#stocklist = ['MQG','CBA']
#stocklist = ['QAN','ATEC','VAS','NDQ']
stocks = [i + '.AX' for i in stocklist]

In [4]:
# Use the Daily Opening data
import fix_yahoo_finance as yf
df_all = yf.Ticker(stocks, start,end)
df_price = df_all['Open'].copy()
df = df_all['Open'].copy()

# Display Stock Info
df.plot()

c:\users\andre\appdata\local\programs\python\python39\lib\site-packages\fix_yahoo_finance\__init__.py:0: DeprecationWarning:



*** `fix_yahoo_finance` was renamed to `yfinance`. ***
Please install and use `yfinance` directly using `pip install yfinance -U`

More information: https://github.com/ranaroussi/yfinance




[*********************100%***********************]  9 of 9 completed


In [5]:
# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / (df[stock].rolling(window, min_periods = 0).median()) - 1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / (df[stock].rolling(window, min_periods = 0).mean()-1)
    return new_df

gradient = norm_df_med(df,window = 20, stocks = stocks)
gradient.plot()

def std_data(data, n = 365, percentage = '50%'):
    data_yr = data[data.index > end - dt.timedelta(days = n)].copy()
    for i in stocks:
        median = data_yr.describe(percentiles=[0.1,0.5,0.9])[i][percentage]
        print(i,median)
        data_yr[i] = data_yr.loc[:,(i)].div(median)
    return data_yr
st = std_data(df)
st.plot()

df['MQG.AX'].pct_change().plot(kind='hist')

## Ch 1.2i: Quick testing algorithm


In [6]:
def final_results(df, stocks = stocks):
    final_array = []
    for stock in stocks:
        final_array.append(round(df[stock][-1],5))
    print('Stocks: ',stocks)
    print('Results:',final_array)
    print('Average: {}'.format(round(sum(final_array)/len(final_array),2)))

## Ch 1.3 Standard Models to Compare 
This section is prebuilt algorithms (from scratch) that are common trading strategies. It is important to compare your proposed model/algorithm against these standards as we want our model to be smarter than the more common trading strategies.

Be sure to use the appropriate Standard model for your assumptions

###  Ch 1.3a Buy and Hold
The Classic buy at the start of your trading period and sell on the last day

This is a very good strategy when you have a large sum of money at the start of your trading period

In [7]:
def buy_n_hold(p_df, stocks = stocks, mode = 'value', total_investment = 8000, brokerage_fee = 20):
    price_df = p_df
    df = pd.DataFrame(index = p_df.index)
    new_df = df
    
    for stock in stocks:
        initial = price_df[stock][0]
        final = price_df[stock][-1]
        step = (final - initial) / len(new_df)
        value_array = []
        percentage_array = []

        if total_investment != None:
            stock_num = (total_investment - brokerage_fee) / initial
            for day_index in range(len(price_df[stock])):
                current_value = (initial + step * day_index) 
                value_array.append(current_value * stock_num)
                percentage_array.append(((current_value / initial) - 1) * 100)
        elif total_investment == None:
            for day_index in range(len(price_df[stock])):
                current_value = initial + step * day_index
                value_array.append(current_value)
                percentage_array.append(((current_value / initial) - 1) * 100)

        if mode == 'value':
            new_df[stock] = value_array
        elif mode == 'percentage':
            new_df[stock] = percentage_array
    return new_df
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = 7000, stocks = stocks)
final_results(bnh)
#bnh.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX', 'ANZ.AX']
Results: [28.82596, 28.00726, 31.70932, 17.71625, -6.9626, 27.20308, 6.25205, 8.30633, 4.96889]
Average: 16.23


### Ch 1.3b Dollar Cost Average
A strict stategy where you input the same fixed value for a specific period. The idea is that you purchase more stocks when the market is down, and purchase less stocks when the market is up.

This strategy is good for investors who have a steady stream of income they want to invest in and if the market is continuously going up

In [8]:
def doll_cost_av(p_df = df_price, day_freq = 60, trade_amount = 5000, stocks = stocks, brokerage_fee = 20, 
                 mode = 'value'):
    new_df = pd.DataFrame(index = p_df.index)
    price_df = p_df
    inv_amount = 0
    inv_array = []
    inv_counter = 0
    for time_index in price_df[stocks].index:
        # trade on the first day
        if len(inv_array) == 0:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter != day_freq: 
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter == day_freq:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter = 0
    #print(inv_array)
    new_df['invested'] = inv_array

    # dollar cost average
    for stock in stocks:
        price_amount = 0
        price_array = []
        day_counter = 0
        stock_amount = 0
        value_delta_array = []
        for time_index in price_df[stocks].index:
            if len(price_array) == 0:
                price_amount += trade_amount
                #print(stock,time_index,price_df[stock][time_index])
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(price_amount)
                value_delta_array.append(0)
                day_counter += 1
            elif day_counter != day_freq: 
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter += 1
            elif day_counter == day_freq:
                price_amount += trade_amount
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter = 0
            #print(price_amount)
            
        if mode == 'percentage':
            new_df[stock] = ((price_array / new_df['invested']) -1 )* 100 
        elif mode == 'value':
            new_df[stock] = price_array
        elif mode == 'value_delta':
            new_df[stock] = value_delta_array
    if mode == 'percentage' or mode == 'value_delta':
        new_df.drop(columns=['invested'], inplace=True)
    
    return new_df

dca = doll_cost_av(p_df = df, mode = 'percentage', stocks = stocks)
final_results(dca)
#dca.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX', 'ANZ.AX']
Results: [6.73412, 9.55087, 9.87566, 1.31983, -12.64254, 26.11678, -0.31363, 0.67304, -6.47496]
Average: 3.87


# Ch 2: Building a New Algorithm

## Ch 2.1: First Algorithm
We standardise each stock performance by dividing it by the rolling median/mean (so we can compare each stock). 

Realising the area under this transformed graph is a better indicator for stock market value. This shows the overall growth of the stock.

Since stock values a year ago is less important information for us than stock values last week, we must include a reduction factor.

We will then put a make a threshold for the new graph and determine when to trade.

In [9]:
# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / (df[stock].rolling(window, min_periods = 0).median()) - 1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / (df[stock].rolling(window, min_periods = 0).mean()-1)
    return new_df

gradient = norm_df_med(df,window = 20, stocks = stocks)
gradient.plot()

In [10]:
# Inputs: normalised stock prices df
# Outputs: area under the graph with a reduction factor df

def norm_sum_df(gradient, reduction_factor  = 1 , stocks = stocks):
    new_df = pd.DataFrame(index = gradient.index)
    for stock in stocks:
        totals = []
        rolling_sum = 0
        for time_index in df.index:
            rolling_sum = (rolling_sum * reduction_factor + gradient[stock][time_index])
            totals.append(rolling_sum)
        new_df[stock] = totals
    return new_df
integral = norm_sum_df(gradient = gradient, reduction_factor = 0.9, stocks = stocks)
integral.plot()

In [11]:
# Input: 2 dfs, the first being the transformed df and another being the df with pricing
#        can also input upper and lower threshholds

# Output: df that determines to trade or not based on threshholds
#         also outputs stock price for each given day

def decision_1(integral = integral, df_price = df_price, stocks = stocks, 
               up_thresh = 0.9, low_thresh = 0.25, thresh_window = 180, trig_thresh = 20):
    decisions = pd.DataFrame(index = integral.index)
    for stock in stocks:
        #trim_df = df[df.index > end - start]
        trim_df = integral
        n_df = integral
        #trim_df_price = df_price[df_price.index > end - start]
        trim_df_price = df_price
        #n_df = (trim_df)

        new_df = pd.DataFrame(index = integral.index)
        new_df['price'] = df_price[stock]
        new_df['norm'] = integral[stock]
        new_df['up_bound'] = integral[stock].rolling(thresh_window, min_periods = 0).quantile(up_thresh).copy()
        new_df['low_bound'] = integral[stock].rolling(thresh_window, min_periods = 0).quantile(low_thresh).copy()

        trade = []
        buy_trig, sell_trig = 0, 0   
        cooler_counter = 0
        for time_index in integral[stock].index:
            if integral[stock][time_index] > new_df['up_bound'][time_index] and sell_trig == 0 and cooler_counter > 10:
                sell_trig = 1
                trade.append(1)
            elif integral[stock][time_index] < new_df['low_bound'][time_index] and buy_trig == 0 and cooler_counter > 10:
                buy_trig = 1
                trade.append(-1)
            else:
                trade.append(0)
            cooler_counter+=1

            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                buy_trig = 0 

        new_df['trade'] = trade
        decisions[stock] = trade
    return decisions
decide = decision_1(integral = integral, df_price = df_price, stocks = stocks,up_thresh = 0.6, low_thresh = 0.4, thresh_window = 180,
                    trig_thresh = 20)
#decide.plot()

In [46]:
def trade_price_df(price_df = df_price, decision_trade_df = df, brokerage_fee = 20, 
                   trade_amount = 6000, compound_factor = None, bank = 8000, mode = 'percentage',
                  stocks = stocks):
    bank_initial = bank
    print('Trade Output:', mode)
    #print(decision_trade_df)
    new_df = pd.DataFrame(index = decision_trade_df.index)

    #if trade_amount > 10000:
    #    brokerage_fee = 30
    for stock in stocks:
        bank = bank_initial
        if compound_factor != None:
            trade_amount = compound_factor * bank
        holding_stocks = 0
        bank_value = []
        total_value = []
        for date_index in decision_trade_df[stock].index:
            if (decision_trade_df[stock][date_index] == -1) & (bank >= trade_amount): 
                # print('buy')
                bank += - trade_amount
                holding_stocks += (trade_amount - brokerage_fee) / price_df[stock][date_index]
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            elif (decision_trade_df[stock][date_index] == 1) and (holding_stocks > 0):
                # print('sell')
                bank += holding_stocks * price_df[stock][date_index] - brokerage_fee
                holding_stocks = 0
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            bank_value.append(bank)
            if math.isnan(price_df[stock][date_index]) == True:
                total_value.append(bank +  holding_stocks * price_df[stock][date_index])
            else:
                total_value.append(bank + holding_stocks * price_df[stock][date_index])
        last_index = -1
        while math.isnan(price_df[stock][last_index]) == True:
            last_index += -1
        else:
            bank_value[-1] = bank + holding_stocks * int(price_df[stock][last_index])
            #print(stock,bank_value[-21],bank_value[-1])
        
        if mode == 'value':
            new_df[stock] = total_value
        elif mode == 'bank':
            new_df[stock] = bank_value
        elif mode == 'percentage':
            new_df[stock] = ((np.array(total_value) / bank_initial) -1) * 100
    return(new_df)


### Ch 2.1a: Run Algorithm 1

In [48]:
stocks_var = stocks
# Gradient
window = 20

# Integral
integral_reduction_factor = 0.9

# Decide
low_thresh = 0.1
up_thresh = 0.6
thresh_window = 60
trade_delay = 20

# Trading
brokerage_fee = 20
compound_factor = 1
amount_per_trade = 6000
bank = 8000
mode = 'percentage'

gradient = norm_df_med(df, window = window, stocks = stocks_var)
integral = norm_sum_df(gradient = gradient, reduction_factor = integral_reduction_factor, stocks = stocks_var)
decide_1 = decision_1(integral = integral, df_price = df_price, stocks = stocks_var,
                      low_thresh = low_thresh, up_thresh = up_thresh , thresh_window = thresh_window, 
                      trig_thresh = trade_delay)
price_1 = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks_var, mode = mode,
                         brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                         compound_factor = compound_factor, bank = bank)
final_results(price_1)
price_1.plot()

Trade Output: percentage
Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX', 'ANZ.AX']
Results: [6.00301, 33.17405, 22.73588, -9.1818, 5.51423, 20.21467, -5.99486, -7.38902, 6.61918]
Average: 7.97


# Ch 2.2: Second Algorithm
We will use the standardised rolling median as well as the integral function to work out the best trading pattern.

Using the rolling median graph as the gradient, we can determine when the graph intercepts with the horizontal axis and thus finding the dip of the area graph. Once that has occured we need to set a threshold for the area graph beyond which will trade to remove any uneccesary trades

In [14]:
# Same as Chapter 2.1

# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / df[stock].rolling(window, min_periods = 0).median() -1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / df[stock].rolling(window, min_periods = 0).mean()-1
    return new_df

gradient = norm_df_med(df,window = 20, stocks = stocks)
#gradient.plot()

In [15]:
# Same as Chapter 2.1

# Inputs: normalised stock prices df
# Outputs: area under the graph with a reduction factor df

def norm_sum_df(gradient, reduction_factor  = 1 , stocks = stocks):
    new_df = pd.DataFrame(index = gradient.index)
    for stock in stocks:
        totals = []
        rolling_sum = 0
        for time_index in df.index:
            rolling_sum = (rolling_sum * reduction_factor + gradient[stock][time_index])
            totals.append(rolling_sum)
        new_df[stock] = totals
    return new_df
integral = norm_sum_df(gradient = gradient, reduction_factor = 0.9, stocks = stocks)
#integral.plot()

In [16]:
def norm_int_df(norm_df, stocks = stocks):
    new_df = pd.DataFrame(index = norm_df.index)
    for stock in stocks:
        crossing_array = []
        for time_index in range(len(norm_df[stock])):
            if time_index == 0:
                crossing_array.append(0)
            elif norm_df[stock][time_index - 1] < 0 and norm_df[stock][time_index] >= 0:
                # indicate to buy
                crossing_array.append(-1)
            elif norm_df[stock][time_index - 1] >= 0 and norm_df[stock][time_index] < 0:
                # indicate to sell
                crossing_array.append(1)
            else: 
                crossing_array.append(0)
        new_df[stock] = crossing_array
    return new_df
intercept = norm_int_df(gradient, stocks = stocks)
#intercept.plot()          

In [17]:
# Input: intercept indicator df and normalised area df
# Output: trade df 
# Gradient = 0, check area graph if its large enough, then buy/sell

def decision_2(norm_int_df = intercept, norm_sum_df = integral, limit_factor = 1, stocks = stocks,
                     trig_thresh = 20):
    new_df = pd.DataFrame(index = norm_int_df.index)
    for stock in stocks:
        trade_array = []
        pos_limit, neg_limit = [],[]
        upper_limit, lower_limit = 0,0
        buy_trig, sell_trig, cooler_counter = 0, 0, 0
        for time_index in range(len(norm_int_df)):
            if norm_sum_df[stock][time_index] >= 0:
                pos_limit.append(norm_sum_df[stock][time_index])
                upper_limit = sum(pos_limit)/len(pos_limit)
            elif norm_sum_df[stock][time_index] < 0:
                neg_limit.append(norm_sum_df[stock][time_index])
                lower_limit = sum(neg_limit)/len(neg_limit)
                
            #print(upper_limit,lower_limit)
            if norm_int_df[stock][time_index] == 1 and norm_sum_df[stock][time_index] > limit_factor * upper_limit and sell_trig == 0 and cooler_counter > 5:
                upper_limit = norm_sum_df[stock][time_index]
                trade_array.append(1)
                sell_trig = 1
            elif norm_int_df[stock][time_index] == -1 and norm_sum_df[stock][time_index] < limit_factor * lower_limit and buy_trig == 0 and cooler_counter > 5:
                lower_limit = norm_sum_df[stock][time_index]
                trade_array.append(-1)
                buy_trig = 1
            else:
                trade_array.append(0)
            
            cooler_counter += 1
               
            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                
                buy_trig = 0 
        new_df[stock] = trade_array
    return(new_df)
decide_2 = decision_2(norm_int_df = intercept, norm_sum_df = integral, stocks = stocks)
#decide_2.plot()

In [49]:
def trade_price_df(price_df = df_price, decision_trade_df = df, brokerage_fee = 20, 
                   trade_amount = 6000, compound_factor = None, bank = 8000, mode = 'percentage',
                  stocks = stocks):
    bank_initial = bank
    print('Trade Output:', mode)
    #print(decision_trade_df)
    new_df = pd.DataFrame(index = decision_trade_df.index)

    #if trade_amount > 10000:
    #    brokerage_fee = 30
    for stock in stocks:
        bank = bank_initial
        if compound_factor != None:
            trade_amount = compound_factor * bank
        holding_stocks = 0
        bank_value = []
        total_value = []
        for date_index in decision_trade_df[stock].index:
            if (decision_trade_df[stock][date_index] == -1) & (bank >= trade_amount): 
                # print('buy')
                bank += - trade_amount
                holding_stocks += (trade_amount - brokerage_fee) / price_df[stock][date_index]
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            elif (decision_trade_df[stock][date_index] == 1) and (holding_stocks > 0):
                # print('sell')
                bank += holding_stocks * price_df[stock][date_index] - brokerage_fee
                holding_stocks = 0
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            bank_value.append(bank)
            
            if math.isnan(price_df[stock][date_index]) == True:
                total_value.append(bank)
            else:
                total_value.append(bank + holding_stocks * int(price_df[stock][date_index]))
        last_index = -1
        while math.isnan(price_df[stock][last_index]) == True:
            last_index += -1
        else:
            bank_value[-1] = bank + holding_stocks * price_df[stock][last_index]
            #print(stock,bank_value[-21],bank_value[-1])
        
        if mode == 'value':
            new_df[stock] = bank_value
        elif mode == 'bank':
            new_df[stock] = total_value
        elif mode == 'percentage':
            new_df[stock] = ((np.array(total_value) / bank_initial) -1) * 100
    return(new_df)

### Ch 2.2a Run Algorithm 2

In [50]:
stocks_var = stocks
# Gradient
window = 20

# Integral
integral_reduction_factor = 0.9

# Decide
limit_factor = 1

# Trading
brokerage_fee = 20
compound_factor = 1
amount_per_trade = 6000
bank = 8000
mode = 'percentage'

gradient = norm_df_med(df, window = window, stocks = stocks_var)
integral = norm_sum_df(gradient = gradient, reduction_factor = integral_reduction_factor, stocks = stocks_var)
intercept = norm_int_df(gradient, stocks = stocks)
decide_2 = decision_2(norm_int_df = intercept, norm_sum_df = integral, stocks = stocks, limit_factor = limit_factor)
price_2 = trade_price_df(price_df = df_price, decision_trade_df = decide_2, stocks = stocks_var, mode = mode,
                         brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                         compound_factor = compound_factor, bank = bank)

final_results(price_2)

Trade Output: percentage
Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX', 'ANZ.AX']
Results: [6.30389, 16.79997, 2.67074, 2.90008, -5.90793, 50.10049, 3.64106, 3.99962, -16.50071]
Average: 7.11


## Ch 3: Analyse Algorithms
We have built a few algorithms now. This next section will analyst and compare the algorithms.

### Ch 3.1: Comparisons
Compare the final value of 2 algorithms performance

In [20]:
def compare_results(df_1, df_2, stocks = stocks, mode = 'percentage'):
    df_1_results = []
    df_2_results = []
    for stock in stocks:
        df_1_results.append(round(df_1[stock][-1],6))
        df_2_results.append(round(df_2[stock][-1],6))
    print('Stocks name:', stocks)
    print('Algorithm 1:', df_1_results)
    print('Algorithm 2:', df_2_results)
    stats_comparison = []
    for i in range(len(df_1_results)):
        stats_comparison.append(round(df_1_results[i] - df_2_results[i],6))
    print('Difference :', stats_comparison)
    if mode == 'percentage':
        print('Average    : {}%'.format(round(sum(stats_comparison)/len(stats_comparison),2)))  
    elif mode == 'value':
        print('Average    : ${}'.format(round(sum(stats_comparison)/len(stats_comparison),2)))
compare_results(df_1 = price_1, df_2 = price_2, stocks = stocks, mode = 'percentage') 

Stocks name: ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX', 'ANZ.AX']
Algorithm 1: [6.334391, 20.377937, 14.138259, -5.21651, 5.431276, 9.574763, -4.245468, -4.934351, 5.181111]
Algorithm 2: [6.303892, 16.799968, 2.670738, 2.900078, -5.907935, 50.100491, 3.641063, 3.999621, -16.500709]
Difference : [0.030499, 3.577969, 11.467521, -8.116588, 11.339211, -40.525728, -7.886531, -8.933972, 21.68182]
Average    : -1.93%


### Ch 3.2: Running Bank total

In [21]:
def risk_stats(decide = decide_1, df_price = df_price, stocks = stocks, mode = 'value', 
              brokerage_fee = 20, trade_amount = 6000, compound_factor = None, bank = 8000, output = False):
    wallet_df = pd.DataFrame(index = df_price.index)
    value_price = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks, mode = mode,
                   brokerage_fee = brokerage_fee, trade_amount = trade_amount, 
                   compound_factor = compound_factor, bank = bank)
    total_array = []
    for time_index in wallet_df.index:
        total_array.append(sum(sum(value_price[value_price.index == time_index].values)))
    wallet_df['running_total'] = total_array
    wallet_df['running_total'].plot()
    fin = wallet_df['running_total'][-1]/(bank*len(stocks))
    most = wallet_df['running_total'].max()/(bank*len(stocks))
    least = wallet_df['running_total'].min()/(bank*len(stocks))
    if output == True:
        print('Statistics for over-all')
        print('Finishing percentage: {}%'.format(round((fin-1)*100,2)))
        print('Highest Percentage:   {}%'.format(round((most-1)*100,2)))
        #print('Lowest Percentage:   {}%'.format(round((least-1)*100,2)))
    return(wallet_df)

wallet = risk_stats(decide = decide_1, df_price = df_price, output = True,
                    compound_factor = compound_factor, bank = bank, trade_amount = amount_per_trade, 
                    brokerage_fee = brokerage_fee)
1
#wallet.plot()

Trade Output: value
Statistics for over-all
Finishing percentage: 5.18%
Highest Percentage:   10.73%


1

## Ch 3.3: Plotting Algorithms

In [52]:
def plotting_results(df_price = df_price, integral = integral, decide = decide_1, price = price_1, 
                     stock = stocks):
    over_all = risk_stats(decide = decide_1, df_price = df_price, compound_factor = 1, output = False)
    cols = plotly.colors.DEFAULT_PLOTLY_COLORS
    k=0
    fig_results = make_subplots(rows = 5, cols = 1, shared_xaxes = True,
                       vertical_spacing = 0.1, subplot_titles = ('Bank Stocks','Normalised Stocks'),
                       row_width = [1,1,1,1,1])
    for stock in stocks:
        fig_results.add_trace(go.Scatter(x = df_price.index, y = df_price[stock], name = stock, 
                                           legendgroup = stock, marker=dict(color=cols[k])), row =1, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = integral[stock], name = stock, 
                                           showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =2, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = decide[stock], name = stock, 
                                          showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =3, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = price_1[stock], name = stock, 
                                           showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =4, col = 1)
        k += 1
    fig_results.add_trace(go.Scatter(x = df_price.index, y = over_all['running_total'], name = 'wallet', 
                                   legendgroup = 'wallet', marker=dict(color=cols[k])), row =5, col = 1)
    fig_results.show()
plotting_results(df_price = df_price, integral = integral, decide = decide_1, price = price_1, stock = stocks)
plotting_results(df_price = df_price, integral = integral, decide = decide_2, price = price_2, stock = stocks)

Trade Output: value


Trade Output: value


Need to finish this
def compare_graphs(df1, df2):
    

### Ch 2.1c: Graphing Results
Graphing

# Notes Past This Point

a = trade_list(df, stock = 'NAB.AX', start = dt.timedelta(days = 365))
trading_results(a)['value'].plot()

In [23]:
#a['up_bound'].plot()

In [24]:
fig_test.update_layout(
    title = 'Trading Data',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Percentage Gain',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)

NameError: name 'fig_test' is not defined

## Graphing Multiple graphs

In [ ]:
print(new_df)

In [ ]:
import datetime as dt
import pandas as pd
from pandas_datareader import data as pdr
import plotly.offline as pyo
import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)

In [ ]:
end = dt.datetime.now()
start = dt.datetime(2015,1,1)

df = yf.Ticker('CBA.AX', start,end)
df.head

In [ ]:
df['MA50'] = df['Close'].rolling(window = 50, min_periods = 0).mean()
df['MA200'] = df['Close'].rolling(window = 200, min_periods = 0).mean()

df['ME30'] = df['Close'].rolling(window = 30, min_periods = 0).median()


In [ ]:
fig = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [ ]:
fig.add_trace(go.Candlestick(x = df.index, open= df['Open'], high = df['High'], low = df['Low'], close = df['Close'], 
                             name = 'OHLC'
                            ),row = 1, col = 1)
1

In [ ]:
fig.add_trace(go.Scatter(x=df.index, y = df['MA50'], marker_color = 'grey', name = 'MA50'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['MA200'], marker_color = 'lightgrey', name = 'MA200'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['ME30'], marker_color = 'blue', name = 'ME30'), row =1, col = 1)
1

In [ ]:
fig.add_trace(go.Bar(x = df.index, y = df['Volume'], marker_color = 'red', showlegend = False), row = 2, col = 1)
1

In [ ]:
fig.update_layout(
    title = 'CBA historical price chart',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Price ($/share)',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)
1

In [ ]:
fig.update(layout_xaxis_rangeslider_visible = False)

In [ ]:
fig_test = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [ ]:
a=[3,90,3,7,8,100]
if [sum(a)<100]:
    a.append(2)
print(a)

In [ ]:
a=[3,90,3,7,8,100]
if sum(a)<100:
    a.append(2)
print(a)